<a href="https://colab.research.google.com/github/Ash-Gayden/Ash-Gayden.github.io/blob/main/Draft_Visualizations.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Visualization made on Altair

# Installs

In [ ]:
%pip install -U "vegafusion[embed]"
%pip install geopandas
%pip install geojson
import pandas as pd
import altair as alt
import vegafusion as vf
from vega_datasets import data
import numpy as np
import matplotlib
%matplotlib inline
import matplotlib.pyplot as plt
plt.style.use('fivethirtyeight')
import json
import geojson
import geopandas as gpd

# Car Dataset Ward Visualizations

In [ ]:
url = 'https://cdn.jsdelivr.net/npm/vega-datasets@1/data/cars.json'
data = pd.read_json(url)
data.head(5)

Name  Miles_per_Gallon  Cylinders  Displacement  \
0  chevrolet chevelle malibu              18.0          8         307.0   
1          buick skylark 320              15.0          8         350.0   
2         plymouth satellite              18.0          8         318.0   
3              amc rebel sst              16.0          8         304.0   
4                ford torino              17.0          8         302.0   

   Horsepower  Weight_in_lbs  Acceleration        Year Origin  
0       130.0           3504          12.0  1970-01-01    USA  
1       165.0           3693          11.5  1970-01-01    USA  
2       150.0           3436          11.0  1970-01-01    USA  
3       150.0           3433          12.0  1970-01-01    USA  
4       140.0           3449          10.5  1970-01-01    USA

In [ ]:
# creating a scatterplot of horsepower by country of origin, with a
# tooltip to list the car's make and model, hp, and origin on mouseover
scatter_plot = alt.Chart(data).mark_circle(size=60).encode(
    x='Origin',
    y='Horsepower',
    color='Origin',
    tooltip=['Name', 'Horsepower', 'Origin']
).properties(
    width=400,
    height=300
)

scatter_plot

alt.Chart(...)

In [ ]:
# creating a heatmap of origin vs cylinders with a tooltip that lists
# the average horsepower and miles per gallon within each heatmap rectangle
avg_data = data.groupby(['Origin', 'Cylinders']).agg({'Horsepower': 'mean', 'Miles_per_Gallon': 'mean'}).reset_index()

# Create heatmap
heatmap = alt.Chart(avg_data).mark_rect().encode(
    x='Cylinders:O',
    y='Origin:O',
    color='Horsepower:Q',
    tooltip=['Horsepower:Q', 'Miles_per_Gallon:Q']
).properties(
    width=400,
    height=300
)

heatmap

alt.Chart(...)

In [ ]:
# creating a scatterplot where clicked points are highlighted and labeled with text
pts = alt.selection_multi()
scatter_plot = alt.Chart(data).mark_circle(size=60).encode(
    x='Horsepower:Q',
    y='Miles_per_Gallon:Q',
    color=alt.condition(pts, alt.value("orange"), alt.value("grey")),
    tooltip=['Name', 'Horsepower', 'Origin'],
).add_selection(pts).interactive()

text_labels = alt.Chart(data).mark_text(align='left',
    baseline='bottom'
    ).encode(
    text=alt.condition(pts, 'Name', alt.value(''))
)

scatter_plot + text_labels

alt.LayerChart(...)

In [ ]:
# creating a scatterplot matrix of horsepower, miles per gallon, displacement, and cylinders
# users should be able to brush points in one chart and filter to highlight those points in other charts
selection = alt.selection_single(fields=['Horsepower', 'Miles_per_Gallon', 'Displacement', 'Cylinders'])

scatter_matrix = alt.Chart(data).mark_point().encode(
    alt.X(alt.repeat('column'), type='quantitative'),
    alt.Y(alt.repeat('row'), type='quantitative'),
    color=alt.condition(selection, alt.value('orange'), alt.value('lightgray')),
    tooltip=['Name', 'Origin']
).properties(
    width=150,
    height=150
).repeat(
    row=['Horsepower', 'Miles_per_Gallon', 'Displacement', 'Cylinders'],
    column=['Horsepower', 'Miles_per_Gallon', 'Displacement', 'Cylinders']
).add_selection(selection)

scatter_matrix

alt.RepeatChart(...)

In [ ]:
# creating bar charts of counts showing the distributions of horsepower, miles per gallon, displacement, and cylinders
# link these bar charts so that the user can brush a filter on all charts simultaniously

selection = alt.selection_multi(fields=['Horsepower', 'Miles_per_Gallon', 'Displacement', 'Cylinders'])

# Create the bar charts
bar_charts = alt.Chart(data).mark_bar().encode(
    x=alt.X(alt.repeat('column'), type='quantitative', bin=True),
    y='count()',
    color=alt.condition(selection, alt.value('orange'), alt.value('lightgray'))
).properties(
    width=200,
    height=150
).repeat(
    column=['Horsepower', 'Miles_per_Gallon', 'Displacement', 'Cylinders']
).add_selection(selection)



bar_charts


alt.RepeatChart(...)

# Insurance Dataset Visualizations

In [ ]:
df= pd.read_csv('/insurance.csv')
df

age     sex     bmi  children smoker     region      charges
0      19  female  27.900         0    yes  southwest  16884.92400
1      18    male  33.770         1     no  southeast   1725.55230
2      28    male  33.000         3     no  southeast   4449.46200
3      33    male  22.705         0     no  northwest  21984.47061
4      32    male  28.880         0     no  northwest   3866.85520
...   ...     ...     ...       ...    ...        ...          ...
1333   50    male  30.970         3     no  northwest  10600.54830
1334   18  female  31.920         0     no  northeast   2205.98080
1335   18  female  36.850         0     no  southeast   1629.83350
1336   21  female  25.800         0     no  southwest   2007.94500
1337   61  female  29.070         0    yes  northwest  29141.36030

[1338 rows x 7 columns]

In [ ]:
# Load the dataset
data = df
# Scatter plot of BMI vs. charges with uncertainty intervals
scatter_plot = alt.Chart(data).mark_circle(size=60).encode(
    x='bmi:Q',
    y='charges:Q',
    color=alt.Color('smoker:N', scale=alt.Scale(scheme='category10')),  # Color points by smoker status
    tooltip=['bmi:Q', 'charges:Q']
).properties(
    width=500,
    height=400
)

# Box plot of charges by smoker status with uncertainty intervals
box_plot = alt.Chart(data).mark_boxplot().encode(
    x='smoker:N',
    y='charges:Q',
    color=alt.Color('smoker:N', scale=alt.Scale(scheme='category10')),  # Color boxes by smoker status
    tooltip=['smoker:N', 'charges:Q']
).properties(
    width=200,
    height=400
)

# Combine the scatter plot and box plot
visualization = (scatter_plot | box_plot).configure_axis(
    labelFontSize=12,
    titleFontSize=14
)

# Display the visualization
visualization

alt.HConcatChart(...)

In [ ]:
# Scatter plot of BMI vs. charges with uncertainty intervals
scatter_plot = alt.Chart(data).mark_circle(size=60).encode(
    x=alt.X('bmi:Q', title='BMI'),
    y=alt.Y('charges:Q', title='Charges'),
    color=alt.Color('smoker:N', scale=alt.Scale(scheme='category10')),  # Color points by smoker status
    tooltip=['bmi:Q', 'charges:Q']
).properties(
    width=300,
    height=300
)

# Marginal histograms of BMI and charges
histograms = alt.Chart(data).mark_bar().encode(
    x=alt.X('bmi:Q', bin=alt.Bin(maxbins=30), title='BMI'),
    y='count()',
    color=alt.Color('smoker:N', scale=alt.Scale(scheme='category10')),  # Color bars by smoker status
    column='smoker:N'
).properties(
    width=300,
    height=100
)

# Combine the scatter plot and histograms
visualization = (scatter_plot | histograms).configure_axis(
    labelFontSize=12,
    titleFontSize=14
).configure_legend(
    labelFontSize=12,
    titleFontSize=14
)

# Display the visualization
visualization


alt.HConcatChart(...)

In [ ]:

# Layered Histogram of BMI and charges
histogram = alt.Chart(data).transform_fold(
    ['charges', 'charges'], as_=['Variable', 'Value']
).mark_bar(opacity=0.7).encode(
    x=alt.X('Value:Q', bin=alt.Bin(maxbins=30), title='Value'),
    y='count()',
    color='smoker:N'
).properties(
    width=400,
    height=300
)

# Display the histogram
histogram

alt.Chart(...)

# Metro-Atlanta Public transit stops

In [ ]:
# https://arc-garc.opendata.arcgis.com/datasets/GARC::transit-routes-2023/about

In [ ]:
from vega_datasets import data
url = 'https://arcgis.atlantaregional.com/arcgis/rest/services/OpenData/FeatureServer/146/query?outFields=*&where=1%3D1&f=geojson'
hello= 'https://services.arcgis.com/xOi1kZaI0eWDREZv/arcgis/rest/services/NTM_Routes/FeatureServer/0?f=pjson'
stops_url = "https://arcgis.atlantaregional.com/arcgis/rest/services/OpenData/FeatureServer/146/query?outFields=*&where=1%3D1&f=geojson"
#stops = alt.topo_feature(stops_url, 'cb_2015_georgia_county_20m')
stop='https://services.arcgis.com/xOi1kZaI0eWDREZv/arcgis/rest/services/NTM_Stops/FeatureServer/0/query?outFields=*&where=1%3D1&f=geojson'
stop_route='https://services.arcgis.com/xOi1kZaI0eWDREZv/arcgis/rest/services/NTM_Routes/FeatureServer/0/query?outFields=*&where=1%3D1&f=geojson'
stops = alt.topo_feature(stop_route, 'features')
ga_url='https://raw.githubusercontent.com/deldersveld/topojson/master/countries/us-states/GA-13-georgia-counties.json'
ga_counties= alt.topo_feature(ga_url, 'cb_2015_georgia_county_20m')

states_data= ga_counties
counties = alt.topo_feature(data.us_10m.url, 'counties')
states= alt.topo_feature(data.us_10m.url, 'states')
source = data.unemployment.url
data1=pd.read_csv('/GDOT_Traffic_Counts_(AADT_and_Truck_Percent)_2008_to_2017.csv')
stop=pd.read_csv('/Transit_Stops_2019.csv')

df=pd.read_csv("/Transit_Routes_2023.csv")
river_url= "https://services.arcgis.com/Tbke9ca9DhtF4VIx/arcgis/rest/services/RockdaleCounty_RiverStream/FeatureServer/6/query?outFields=*&where=1%3D1&f=geojson"
data1=pd.read_csv('/GDOT_Traffic_Counts_(AADT_and_Truck_Percent)_2008_to_2017.csv')
#data1.head(5)


In [ ]:
states = alt.topo_feature(url, 'features')

# Create a chart
chart = alt.Chart(states).mark_geoshape().encode(
    color=alt.Color('properties.name:N', legend=None),
    tooltip=[alt.Tooltip('properties.name:N')]
).properties(
    width=700,
    height=400
)

#chart

In [ ]:
ga_map= alt.Chart(ga_counties).mark_geoshape(
    fill='lightgray',
    stroke='white').encode(
)
#ga_counties
# Create a map chart
ga_map

transit_points = alt.Chart(stops_url).mark_geoshape(
    stroke='gray', strokeWidth=.5).encode(
)
river_points = alt.Chart(river_url).mark_geoshape(
    stroke='lightblue').encode(
)
trying =ga_map + transit_points + river_points
df['rte_type']

stopper=stop.drop_duplicates('stop_name')
Marta=stopper.loc[stopper['agency_nam']=='MARTA',:]
stop1= stopper.loc[stopper['agency_nam']!='MARTA',:]
stop2= Marta.head(3656)
stop3=Marta.tail(3655)
stopper['routes'].value_counts()
df50=df[['agency_id', 'rte_type', 'OBJECTID', 'short_name']]

combo=pd.merge(df50, stop, how='outer', on=['OBJECTID'])
new_combo=combo.loc[pd.notnull(combo['X']),:]
combo.shape, new_combo.shape
combos=new_combo.fillna('unknown')
#stopper=new_combo.drop_duplicates('stop_name')
#Marta=stopper.loc[stopper['agency_nam']=='MARTA',:]
#stop1= stopper.loc[stopper['agency_nam']!='MARTA',:]
#stop2= Marta.head(3656)
#stop3=Marta.tail(3655)
#tryingg=combos['agency_nam_x']==combos['agency_nam_y']
combos.shape #11004,18
#combos
#stop

(11004, 16)

In [ ]:
#states_data = alt.topo_feature(data.us_10m.url, "states")

def create_county_chart(county_code):
    chart = alt.Chart(counties).mark_geoshape(
        stroke='black',
        strokeWidth=1
    ).encode(
        #color='rate:Q'
    ).transform_lookup(
        lookup='id',
        from_=alt.LookupData(source, 'id', ['rate'])
    ).transform_filter((alt.datum.id == county_code))

    return chart
cobb = create_county_chart(13067)
fulton = create_county_chart(13121)
dekalb = create_county_chart(13089)
rockdale = create_county_chart(13247)
douglas = create_county_chart(13097)
fayette = create_county_chart(13113)
henry = create_county_chart(13151)
gwinnett = create_county_chart(13135)
forsyth = create_county_chart(13117)
cherokee = create_county_chart(13057)
clayton = create_county_chart(13063)
metroatl=rockdale + cobb + fulton + dekalb + douglas + fayette + henry + gwinnett + forsyth + cherokee + clayton

stops_layer = alt.Chart(stop2).mark_circle(
    color='agency_nam:N',
    size=2,
).transform_lookup(
    lookup='id',
    from_=alt.LookupData(stop2, 'id', ['agency_nam'])
).encode(
    longitude='X:Q',
    latitude='Y:Q'
)

stops_layer1 = alt.Chart(stop1).mark_circle(
    color='agency_nam:N',
    size=5
).encode(
    longitude='X:Q',
    latitude='Y:Q',
    color=alt.Color('agency_nam:N', scale=alt.Scale(scheme='dark2'), type='ordinal'),
    shape=alt.Shape('rte_type:N')
)
stops_layer2 = alt.Chart(stop2).mark_circle(
    color='agency_nam:N',
    size=5
).encode(
    longitude='X:Q',
    latitude='Y:Q',
    color=alt.Color('agency_nam:N', scale=alt.Scale(scheme='dark2'), type='ordinal')
)
stops_layer3 = alt.Chart(stop3).mark_circle(
    color='agency_nam:N',
    size=5
).encode(
    longitude='X:Q',
    latitude='Y:Q',
    color=alt.Color('agency_nam:N', scale=alt.Scale(scheme='dark2'), type='ordinal')
)
metroatl=rockdale + cobb + fulton + dekalb + douglas + fayette + henry + gwinnett + forsyth + cherokee + clayton

metroatl
transit_stops = stops_layer2+stops_layer1+stops_layer3
transit_stops

alt.LayerChart(...)

In [ ]:
data1=data1[['X',
 'Y',
 'Station_ID',
 'Functional_Class',
 'LatLong',
 'Lat',
 'Long',
 'AADT_2017',
 'TruckPct_2017']]
# Visualization 2: Traffic Congestion Analysis
#annual everyday traffic
scatterplot = alt.Chart(data1).mark_circle().encode(
    x='X:Q',
    y='Y:Q',
    color='AADT_2017:Q'
).properties(
    width=500, height=400,
    title='Traffic Congestion Analysis'
)
scatterplot
data1.drop_duplicates("Station_ID")

sampled_data = data1.sample(n=5000, random_state=42)
datatop=data1.nlargest(110, 'AADT_2017')
# Create an Altair scatter plot
chart = alt.Chart(datatop).mark_circle().encode(
    longitude='X',
    latitude='Y',
    color= alt.Color('AADT_2017', scale=alt.Scale(scheme='viridis')),
    #tooltip=['Station_ID', 'Functional_Class', 'AADT_2017']
).properties(
    width=500, height=400,
    title='Traffic Congestion Analysis'
)
chart




metroatl+transit_stops + chart


alt.LayerChart(...)

# Civilian Complaints Against NYC Police Officers


Visualization 1:

In [ ]:
df= pd.read_csv('/allegations_202007271729.csv')
list(df)
df1=df.drop(columns=['first_name', 'last_name', 'allegation',
 'precinct',
 'contact_reason',
 'outcome_description',
 'board_disposition', 'first_name',
 'last_name',
 'command_now',
 'shield_no',
 'complaint_id','command_at_incident',
 'rank_abbrev_incident',
 'rank_abbrev_now',
 'rank_now',
 'rank_incident',
 'mos_ethnicity','mos_age_incident', 'complainant_age_incident',
 'complainant_ethnicity',])

df1['received']= '1/' +  df1['month_received'].astype(str) + '/' + df1['year_received'].astype(str)
df1['closed']= '1/' + df1['month_closed'].astype(str) + '/' + df1['year_closed'].astype(str)
df1['closed']=pd.to_datetime(df1['closed'], format='%d/%m/%Y')
df1['received']=pd.to_datetime(df1['received'], format='%d/%m/%Y')
df1['Open/Close']= df1['closed'] - df1['received']
df1['Open/Close']= df1['Open/Close'].astype(str)
df1['Days Waited'] = df1['Open/Close'].str.extract('(\d+)').astype(int)

df1['fado_type'].value_counts()
df2=df1
df2=df1[df1['year_received']==2017]

def whynot(df_name):
  chart= alt.Chart(df_name).mark_boxplot().encode(
      x='complainant_gender:N',
      y='Days Waited:Q',
      color='complainant_gender:N',
      tooltip=['fado_type', 'Days Waited', 'complainant_gender']
  ).properties(
      title='Closed Rates for Fado Type by Month and Gender'
  ).configure_axis(
      labelFontSize=12,
      titleFontSize=14
  ).configure_title(
      fontSize=16,
      fontWeight='bold',
      anchor='start'
  ).configure_legend(
      titleFontSize=12,
      labelFontSize=10
  )
  return chart

df2_grouped = df2.groupby(['complainant_gender', 'fado_type'])['Days Waited'].mean().reset_index()

whynot(df2_grouped)
df3_grouped = df1.groupby(['received','complainant_gender', 'fado_type'])['Days Waited'].mean().reset_index()
df3_grouped
whynot(df3_grouped)

alt.Chart(...)

In [ ]:
charts=alt.Chart(df2_grouped).mark_bar().encode(
    color='complainant_gender:N',
    x='Days Waited:Q',
    y='fado_type:N',
    tooltip=['fado_type', 'Days Waited', 'complainant_gender']
).properties(
    title='Closed Rates for Fado Type by Month and Gender'
)
alt.Chart(df3_grouped).mark_bar().encode(
    color='complainant_gender:N',
    x='Days Waited:Q',
    y='fado_type:N',
    tooltip=['fado_type', 'Days Waited', 'complainant_gender']
).properties(
    title='Closed Rates for Fado Type by Month and Gender'
)
alt.Chart(df3_grouped).mark_circle().encode(
    x='complainant_gender:N',
    y='Days Waited:Q',
    color='fado_type:N',
    tooltip=['fado_type', 'Days Waited', 'complainant_gender']
).properties(
    title='Closed Rates for Fado Type by Month and Gender'
)

alt.Chart(...)